In [1]:
# import the modules
import pandas as pd
from pathlib import Path
from pprint import pprint
from sklearn.cluster import KMeans
from sklearn.decomposition import PCA
import matplotlib.pyplot as plt
import hvplot.pandas


In [2]:
#set the file path
file_path = Path('instacart-market-basket-analysis/orders.csv')

#read the csv into a pandas DataFrame
orders_df = pd.read_csv(file_path)

orders_df.head()

order_id  user_id eval_set  order_number  order_dow  order_hour_of_day  \
0   2539329        1    prior             1          2                  8   
1   2398795        1    prior             2          3                  7   
2    473747        1    prior             3          3                 12   
3   2254736        1    prior             4          4                  7   
4    431534        1    prior             5          4                 15   

   days_since_prior_order  
0                     NaN  
1                    15.0  
2                    21.0  
3                    29.0  
4                    28.0

In [3]:
orders_df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 3421083 entries, 0 to 3421082
Data columns (total 7 columns):
 #   Column                  Dtype  
---  ------                  -----  
 0   order_id                int64  
 1   user_id                 int64  
 2   eval_set                object 
 3   order_number            int64  
 4   order_dow               int64  
 5   order_hour_of_day       int64  
 6   days_since_prior_order  float64
dtypes: float64(1), int64(5), object(1)
memory usage: 182.7+ MB


In [4]:
len(orders_df)

3421083

In [5]:
orders_df['eval_set'].unique()

array(['prior', 'train', 'test'], dtype=object)

In [6]:
orders_df['eval_set'].value_counts()

eval_set
prior    3214874
train     131209
test       75000
Name: count, dtype: int64

In [7]:
file_path_prior = Path('instacart-market-basket-analysis/order_products__prior.csv')
prior_df = pd.read_csv(file_path_prior)
prior_df.head()

order_id  product_id  add_to_cart_order  reordered
0         2       33120                  1          1
1         2       28985                  2          1
2         2        9327                  3          0
3         2       45918                  4          1
4         2       30035                  5          0

In [8]:
len(prior_df)

32434489

In [9]:
file_path_train = Path('instacart-market-basket-analysis/order_products__train.csv')
train_df = pd.read_csv(file_path_train)
train_df.head()

order_id  product_id  add_to_cart_order  reordered
0         1       49302                  1          1
1         1       11109                  2          1
2         1       10246                  3          0
3         1       49683                  4          0
4         1       43633                  5          1

In [10]:
len(train_df)

1384617

In [11]:
file_path_products = Path('instacart-market-basket-analysis/products.csv')
products_df = pd.read_csv(file_path_products)
products_df.head()

product_id                                       product_name  aisle_id  \
0           1                         Chocolate Sandwich Cookies        61   
1           2                                   All-Seasons Salt       104   
2           3               Robust Golden Unsweetened Oolong Tea        94   
3           4  Smart Ones Classic Favorites Mini Rigatoni Wit...        38   
4           5                          Green Chile Anytime Sauce         5   

   department_id  
0             19  
1             13  
2              7  
3              1  
4             13

In [12]:
len(products_df)

49688

In [13]:
file_path_aisles = Path('instacart-market-basket-analysis/aisles.csv')
aisles_df = pd.read_csv(file_path_aisles)
aisles_df.head()

aisle_id                       aisle
0         1       prepared soups salads
1         2           specialty cheeses
2         3         energy granola bars
3         4               instant foods
4         5  marinades meat preparation

In [14]:
len(aisles_df)

134

In [15]:
file_path_dept = Path('instacart-market-basket-analysis/departments.csv')
dept_df = pd.read_csv(file_path_dept)
dept_df.head()

department_id department
0              1     frozen
1              2      other
2              3     bakery
3              4    produce
4              5    alcohol

In [16]:
len(dept_df)

21

In [17]:
merged_df_prior_1 = pd.merge(prior_df, products_df, on='product_id', how='left')
merged_df_prior_1.head()

order_id  product_id  add_to_cart_order  reordered           product_name  \
0         2       33120                  1          1     Organic Egg Whites   
1         2       28985                  2          1  Michigan Organic Kale   
2         2        9327                  3          0          Garlic Powder   
3         2       45918                  4          1         Coconut Butter   
4         2       30035                  5          0      Natural Sweetener   

   aisle_id  department_id  
0        86             16  
1        83              4  
2       104             13  
3        19             13  
4        17             13

In [18]:
len(merged_df_prior_1)

32434489

In [19]:
merged_df_prior_2 = pd.merge(merged_df_prior_1, aisles_df, on='aisle_id', how='left')
merged_df_prior_2.head()

order_id  product_id  add_to_cart_order  reordered           product_name  \
0         2       33120                  1          1     Organic Egg Whites   
1         2       28985                  2          1  Michigan Organic Kale   
2         2        9327                  3          0          Garlic Powder   
3         2       45918                  4          1         Coconut Butter   
4         2       30035                  5          0      Natural Sweetener   

   aisle_id  department_id               aisle  
0        86             16                eggs  
1        83              4    fresh vegetables  
2       104             13   spices seasonings  
3        19             13       oils vinegars  
4        17             13  baking ingredients

In [20]:
len(merged_df_prior_2)

32434489

In [21]:
merged_df_prior_3 = pd.merge(merged_df_prior_2, dept_df, on='department_id', how='left')
merged_df_prior_3.head()

order_id  product_id  add_to_cart_order  reordered           product_name  \
0         2       33120                  1          1     Organic Egg Whites   
1         2       28985                  2          1  Michigan Organic Kale   
2         2        9327                  3          0          Garlic Powder   
3         2       45918                  4          1         Coconut Butter   
4         2       30035                  5          0      Natural Sweetener   

   aisle_id  department_id               aisle  department  
0        86             16                eggs  dairy eggs  
1        83              4    fresh vegetables     produce  
2       104             13   spices seasonings      pantry  
3        19             13       oils vinegars      pantry  
4        17             13  baking ingredients      pantry

In [22]:
merged_df_prior_4 = pd.merge(merged_df_prior_3, orders_df, on='order_id', how='left')
merged_df_prior_4.head()

order_id  product_id  add_to_cart_order  reordered           product_name  \
0         2       33120                  1          1     Organic Egg Whites   
1         2       28985                  2          1  Michigan Organic Kale   
2         2        9327                  3          0          Garlic Powder   
3         2       45918                  4          1         Coconut Butter   
4         2       30035                  5          0      Natural Sweetener   

   aisle_id  department_id               aisle  department  user_id eval_set  \
0        86             16                eggs  dairy eggs   202279    prior   
1        83              4    fresh vegetables     produce   202279    prior   
2       104             13   spices seasonings      pantry   202279    prior   
3        19             13       oils vinegars      pantry   202279    prior   
4        17             13  baking ingredients      pantry   202279    prior   

   order_number  order_dow  order_hour_of_day  days_since_prior_order  
0             3          5                  9                     8.0  
1             3          5                  9                     8.0  
2             3          5                  9                     8.0  
3             3          5                  9                     8.0  
4             3          5                  9                     8.0

In [23]:
len(merged_df_prior_4)

32434489

In [24]:
new_column_order = ['user_id', 'order_id', 'product_id', 'product_name', 'aisle_id', 'aisle', 'department_id', 'department']
prior_df_final = merged_df_prior_4[new_column_order]
prior_df_final.head()

user_id  order_id  product_id           product_name  aisle_id  \
0   202279         2       33120     Organic Egg Whites        86   
1   202279         2       28985  Michigan Organic Kale        83   
2   202279         2        9327          Garlic Powder       104   
3   202279         2       45918         Coconut Butter        19   
4   202279         2       30035      Natural Sweetener        17   

                aisle  department_id  department  
0                eggs             16  dairy eggs  
1    fresh vegetables              4     produce  
2   spices seasonings             13      pantry  
3       oils vinegars             13      pantry  
4  baking ingredients             13      pantry

In [25]:
len(prior_df_final)

32434489

In [26]:
# number of unique user_id
unique_user_count = prior_df_final['user_id'].nunique()
print(unique_user_count)

206209


In [27]:
# get information to double check the pivot tables
# how many orders from a specific user
specific_user_id = 1
user_info = prior_df_final[prior_df_final['user_id'] == specific_user_id]
user_info

user_id  order_id  product_id  \
4089398         1    431534         196   
4089399         1    431534       12427   
4089400         1    431534       10258   
4089401         1    431534       25133   
4089402         1    431534       10326   
4089403         1    431534       17122   
4089404         1    431534       41787   
4089405         1    431534       13176   
4488095         1    473747         196   
4488096         1    473747       12427   
4488097         1    473747       10258   
4488098         1    473747       25133   
4488099         1    473747       30450   
5212927         1    550135         196   
5212928         1    550135       10258   
5212929         1    550135       12427   
5212930         1    550135       25133   
5212931         1    550135       13032   
21376074        1   2254736         196   
21376075        1   2254736       12427   
21376076        1   2254736       10258   
21376077        1   2254736       25133   
21376078        1   2254736       26405   
21760443        1   2295261       49235   
21760444        1   2295261       46149   
21760445        1   2295261       25133   
21760446        1   2295261         196   
21760447        1   2295261       10258   
21760448        1   2295261       12427   
22742744        1   2398795         196   
22742745        1   2398795       10258   
22742746        1   2398795       12427   
22742747        1   2398795       13176   
22742748        1   2398795       26088   
22742749        1   2398795       13032   
24076664        1   2539329         196   
24076665        1   2539329       14084   
24076666        1   2539329       12427   
24076667        1   2539329       26088   
24076668        1   2539329       26405   
24181266        1   2550362         196   
24181267        1   2550362       46149   
24181268        1   2550362       39657   
24181269        1   2550362       38928   
24181270        1   2550362       25133   
24181271        1   2550362       10258   
24181272        1   2550362       35951   
24181273        1   2550362       13032   
24181274        1   2550362       12427   
29474805        1   3108588       12427   
29474806        1   3108588         196   
29474807        1   3108588       10258   
29474808        1   3108588       25133   
29474809        1   3108588       46149   
29474810        1   3108588       49235   
31927070        1   3367565         196   
31927071        1   3367565       12427   
31927072        1   3367565       10258   
31927073        1   3367565       25133   

                                     product_name  aisle_id  \
4089398                                      Soda        77   
4089399                       Original Beef Jerky        23   
4089400                                Pistachios       117   
4089401                     Organic String Cheese        21   
4089402                       Organic Fuji Apples        24   
4089403                         Honeycrisp Apples        24   
4089404                            Bartlett Pears        24   
4089405                    Bag of Organic Bananas        24   
4488095                                      Soda        77   
4488096                       Original Beef Jerky        23   
4488097                                Pistachios       117   
4488098                     Organic String Cheese        21   
4488099                      Creamy Almond Butter        88   
5212927                                      Soda        77   
5212928                                Pistachios       117   
5212929                       Original Beef Jerky        23   
5212930                     Organic String Cheese        21   
5212931                     Cinnamon Toast Crunch       121   
21376074                                     Soda        77   
21376075                      Original Beef Jerky        23   
21376076                               Pistachios       117   
21376077                    Organic String 

In [28]:
# total order of orders
user_info.value_counts().sum()

59

In [29]:
# aisle pivot table
aisle_pivot_table = prior_df_final.pivot_table(index='user_id', columns='aisle', values='order_id', aggfunc='count').fillna(0)
aisle_pivot_table.head()

aisle    air fresheners candles  asian foods  baby accessories  \
user_id                                                          
1                           0.0          0.0               0.0   
2                           0.0          3.0               0.0   
3                           0.0          0.0               0.0   
4                           0.0          0.0               0.0   
5                           0.0          2.0               0.0   

aisle    baby bath body care  baby food formula  bakery desserts  \
user_id                                                            
1                        0.0                0.0              0.0   
2                        0.0                0.0              0.0   
3                        0.0                0.0              0.0   
4                        0.0                0.0              0.0   
5                        0.0                0.0              0.0   

aisle    baking ingredients  baking supplies decor  beauty  beers coolers  \
user_id                                                                     
1                       0.0                    0.0     0.0            0.0   
2                       2.0                    0.0     0.0            0.0   
3                       0.0                    0.0     0.0            0.0   
4                       0.0                    0.0     0.0            0.0   
5                       0.0                    0.0     0.0            0.0   

aisle    ...  spreads  tea  tofu meat alternatives  tortillas flat bread  \
user_id  ...                                                               
1        ...      1.0  0.0                     0.0                   0.0   
2        ...      3.0  1.0                     1.0                   0.0   
3        ...      4.0  1.0                     0.0                   0.0   
4        ...      0.0  0.0                     0.0                   1.0   
5        ...      0.0  0.0                     0.0                   0.0   

aisle    trail mix snack mix  trash bags liners  vitamins supplements  \
user_id                                                                 
1                        0.0                0.0                   0.0   
2                        0.0                0.0                   0.0   
3                        0.0                0.0                   0.0   
4                        0.0                0.0                   0.0   
5                        0.0                0.0                   0.0   

aisle    water seltzer sparkling water  white wines  yogurt  
user_id                                                      
1                                  0.0          0.0     1.0  
2                                  2.0          0.0    42.0  
3                                  2.0          0.0     0.0  
4                                  1.0          0.0     0.0  
5                                  0.0          0.0     3.0  

[5 rows x 134 columns]

In [30]:
len(aisle_pivot_table)

206209

In [31]:
#remove the rows to clean the data, remove alcohol
clean_dept_df = prior_df_final[prior_df_final['department'].str.contains('alcohol') == False]

In [32]:
clean_dept_df

user_id  order_id  product_id  \
0          202279         2       33120   
1          202279         2       28985   
2          202279         2        9327   
3          202279         2       45918   
4          202279         2       30035   
...           ...       ...         ...   
32434484    25247   3421083       39678   
32434485    25247   3421083       11352   
32434486    25247   3421083        4600   
32434487    25247   3421083       24852   
32434488    25247   3421083        5020   

                                               product_name  aisle_id  \
0                                        Organic Egg Whites        86   
1                                     Michigan Organic Kale        83   
2                                             Garlic Powder       104   
3                                            Coconut Butter        19   
4                                         Natural Sweetener        17   
...                                                     ...       ...   
32434484          Free & Clear Natural Dishwasher Detergent        74   
32434485       Organic Mini Sandwich Crackers Peanut Butter        78   
32434486                    All Natural French Toast Sticks        52   
32434487                                             Banana        24   
32434488  Organic  Sweet & Salty Peanut Pretzel Granola ...         3   

                        aisle  department_id  department  
0                        eggs             16  dairy eggs  
1            fresh vegetables              4     produce  
2           spices seasonings             13      pantry  
3               oils vinegars             13      pantry  
4          baking ingredients             13      pantry  
...                       ...            ...         ...  
32434484      dish detergents             17   household  
32434485             crackers             19      snacks  
32434486     frozen breakfast              1      frozen  
32434487         fresh fruits              4     produce  
32434488  energy granola bars             19      snacks  

[32280793 rows x 8 columns]

In [33]:
# remove rows with 'babies'
clean_dept_df_2 = clean_dept_df[clean_dept_df['department'].str.contains('babies') == False]

In [34]:
# remove rows with 'bulk'
clean_dept_df_3 = clean_dept_df_2[clean_dept_df_2['department'].str.contains('bulk') == False]

In [35]:
# remove rows with 'missing'
clean_dept_df_4 = clean_dept_df_3[clean_dept_df_3['department'].str.contains('missing') == False]

In [36]:
# remove rows with 'other'
clean_dept_df_5 = clean_dept_df_4[clean_dept_df_4['department'].str.contains('other') == False]

In [37]:
# remove rows with 'pets'
clean_dept_df_final = clean_dept_df_5[clean_dept_df_5['department'].str.contains('pets') == False]
clean_dept_df_final

user_id  order_id  product_id  \
0          202279         2       33120   
1          202279         2       28985   
2          202279         2        9327   
3          202279         2       45918   
4          202279         2       30035   
...           ...       ...         ...   
32434484    25247   3421083       39678   
32434485    25247   3421083       11352   
32434486    25247   3421083        4600   
32434487    25247   3421083       24852   
32434488    25247   3421083        5020   

                                               product_name  aisle_id  \
0                                        Organic Egg Whites        86   
1                                     Michigan Organic Kale        83   
2                                             Garlic Powder       104   
3                                            Coconut Butter        19   
4                                         Natural Sweetener        17   
...                                                     ...       ...   
32434484          Free & Clear Natural Dishwasher Detergent        74   
32434485       Organic Mini Sandwich Crackers Peanut Butter        78   
32434486                    All Natural French Toast Sticks        52   
32434487                                             Banana        24   
32434488  Organic  Sweet & Salty Peanut Pretzel Granola ...         3   

                        aisle  department_id  department  
0                        eggs             16  dairy eggs  
1            fresh vegetables              4     produce  
2           spices seasonings             13      pantry  
3               oils vinegars             13      pantry  
4          baking ingredients             13      pantry  
...                       ...            ...         ...  
32434484      dish detergents             17   household  
32434485             crackers             19      snacks  
32434486     frozen breakfast              1      frozen  
32434487         fresh fruits              4     produce  
32434488  energy granola bars             19      snacks  

[31619258 rows x 8 columns]

In [38]:
# Department pivot table
department_pivot_table = clean_dept_df_final.pivot_table(index='user_id', columns='department', values='order_id', aggfunc='count').fillna(0)
department_pivot_table.head()

department  bakery  beverages  breakfast  canned goods  dairy eggs  deli  \
user_id                                                                    
1              0.0       13.0        3.0           0.0        13.0   0.0   
2              2.0        9.0        3.0           1.0        48.0  21.0   
3              0.0        3.0        0.0           0.0        21.0   2.0   
4              2.0        3.0        0.0           1.0         0.0   2.0   
5              0.0        0.0        0.0           1.0         8.0   1.0   

department  dry goods pasta  frozen  household  international  meat seafood  \
user_id                                                                       
1                       0.0     0.0        2.0            0.0           0.0   
2                       0.0    17.0        0.0            3.0           1.0   
3                       4.0     6.0        1.0            0.0           0.0   
4                       0.0     3.0        2.0            0.0           0.0   
5                       1.0     2.0        0.0            2.0           0.0   

department  pantry  personal care  produce  snacks  
user_id                                             
1              1.0            0.0      5.0    22.0  
2             11.0            1.0     36.0    42.0  
3              4.0            0.0     38.0     9.0  
4              0.0            0.0      2.0     1.0  
5              2.0            0.0     19.0     1.0

In [39]:
len(department_pivot_table)

206140

In [40]:
# how many total items a specific user id bought, double check data from earlier
test_user_id = 1
total_purchased = department_pivot_table.loc[test_user_id].sum()
total_purchased

59.0

In [41]:
# list products purchased by a specific user id, double check data from earlier
total_purchased = department_pivot_table.loc[test_user_id]
total_purchased

department
bakery              0.0
beverages          13.0
breakfast           3.0
canned goods        0.0
dairy eggs         13.0
deli                0.0
dry goods pasta     0.0
frozen              0.0
household           2.0
international       0.0
meat seafood        0.0
pantry              1.0
personal care       0.0
produce             5.0
snacks             22.0
Name: 1, dtype: float64

In [42]:
# AISLE_PIVOT_TABLE_2 (normalized row data)

In [43]:
#normalize rows for aisle data
aisle_pivot_table_2 = aisle_pivot_table.div(aisle_pivot_table.sum(axis=1), axis=0)
aisle_pivot_table_2

aisle    air fresheners candles  asian foods  baby accessories  \
user_id                                                          
1                           0.0     0.000000           0.00000   
2                           0.0     0.015385           0.00000   
3                           0.0     0.000000           0.00000   
4                           0.0     0.000000           0.00000   
5                           0.0     0.054054           0.00000   
...                         ...          ...               ...   
206205                      0.0     0.000000           0.03125   
206206                      0.0     0.014035           0.00000   
206207                      0.0     0.000000           0.00000   
206208                      0.0     0.004431           0.00000   
206209                      0.0     0.007752           0.00000   

aisle    baby bath body care  baby food formula  bakery desserts  \
user_id                                                            
1                        0.0           0.000000              0.0   
2                        0.0           0.000000              0.0   
3                        0.0           0.000000              0.0   
4                        0.0           0.000000              0.0   
5                        0.0           0.000000              0.0   
...                      ...                ...              ...   
206205                   0.0           0.000000              0.0   
206206                   0.0           0.000000              0.0   
206207                   0.0           0.004484              0.0   
206208                   0.0           0.004431              0.0   
206209                   0.0           0.000000              0.0   

aisle    baking ingredients  baking supplies decor  beauty  beers coolers  \
user_id                                                                     
1                  0.000000               0.000000     0.0            0.0   
2                  0.010256               0.000000     0.0            0.0   
3                  0.000000               0.000000     0.0            0.0   
4                  0.000000               0.000000     0.0            0.0   
5                  0.000000               0.000000     0.0            0.0   
...                     ...                    ...     ...            ...   
206205             0.000000               0.000000     0.0            0.0   
206206             0.014035               0.003509     0.0            0.0   
206207             0.000000               0.000000     0.0            0.0   
206208             0.005908               0.000000     0.0            0.0   
206209             0.000000               0.000000     0.0            0.0   

aisle    ...   spreads       tea  tofu meat alternatives  \
user_id  ...                                               
1        ...  0.016949  0.000000                0.000000   
2        ...  0.015385  0.005128                0.005128   
3        ...  0.045455  0.011364                0.000000   
4        ...  0.000000  0.000000                0.000000   
5        ...  0.000000  0.000000                0.000000   
...      ...       ...       ...                     ...   
206205   ...  0.000000  0.000000                0.000000   
206206   ...  0.003509  0.000000                0.000000   
206207   ...  0.013453  0.017937                0.000000   
206208   ...  0.007386  0.000000                0.000000   
206209   ...  0.000000  0.000000                0.000000   

aisle    tortillas flat bread  trail mix snack mix  trash bags liners  \
user_id                                                                 
1                    0.000000             0.000000           0.000000   
2                    0.000000             0.000000           0.000000   
3                    0.000000             0.000000           0.000000   
4                    0.055556             0.000000           0.000000   
5                    0.000000      

In [44]:
# AISLE ELBOW CURVE

In [45]:
#create a list to store inertia values
inertia = []

#create a list to store the values of k
k = list(range(1, 50))

In [46]:
# Create a for-loop where each value of k is evaluated using the K-means algorithm
# Fit the model using the spread_df DataFrame
# Append the value of the computed inertia from the `inertia_` attribute of the KMeans model instance
for i in k:
    k_model = KMeans(n_clusters=i, random_state=1)
    k_model.fit(aisle_pivot_table_2)
    inertia.append(k_model.inertia_)

In [47]:
# Create a Dictionary that holds the list values for k and inertia
elbow_data = {"k": k, "inertia": inertia}

# Create a DataFrame using the elbow_data Dictionary
df_elbow = pd.DataFrame(elbow_data)

# Review the DataFrame
df_elbow

k       inertia
0    1  16760.932473
1    2  15195.608501
2    3  14490.391939
3    4  13660.225386
4    5  13117.784483
5    6  12752.282808
6    7  12435.048741
7    8  12178.950453
8    9  11990.725560
9   10  11934.273808
10  11  11800.040142
11  12  11507.641029
12  13  11332.012485
13  14  11187.559925
14  15  11111.211270
15  16  11026.575214
16  17  10954.598527
17  18  10813.495681
18  19  10710.064616
19  20  10612.697789
20  21  10457.026212
21  22  10381.982845
22  23  10353.410250
23  24  10286.582491
24  25  10215.682968
25  26  10106.859648
26  27  10048.545263
27  28   9974.650923
28  29   9928.389103
29  30   9898.251187
30  31   9865.984563
31  32   9823.501250
32  33   9783.326642
33  34   9763.319813
34  35   9773.515654
35  36   9734.000433
36  37   9666.469209
37  38   9562.288871
38  39   9549.202250
39  40   9502.550205
40  41   9481.217906
41  42   9375.996903
42  43   9325.462062
43  44   9298.445556
44  45   9295.974708
45  46   9241.744552
46  47   9217.360481
47  48   9186.453326
48  49   9152.467524

In [48]:
# Plot the DataFrame
df_elbow.hvplot.line(
    x="k",
    y="inertia",
    title="Elbow Curve",
    xticks=k
)

:Curve   [k]   (inertia)

In [49]:
#setting up the aisle clustering, create and initialize the K-means model for 4 clusters
model = KMeans(n_clusters=25, random_state=1)
model

KMeans(n_clusters=25, random_state=1)

In [50]:
#fit the data to the instance of the model
model.fit(aisle_pivot_table_2)

KMeans(n_clusters=25, random_state=1)

In [51]:
#make predictions about the data cluster the pivot table?
customer_aisle_segs = model.predict(aisle_pivot_table_2)
customer_aisle_segs

array([18, 19,  7, ...,  3,  3, 13])

In [52]:
# create a copy of the DataFrame
customer_aisle_segs_predict_df = aisle_pivot_table_2.copy()

# Add a column to the DataFrame that conains the customer_segmentation information
customer_aisle_segs_predict_df['customer_segments'] = customer_aisle_segs

# review the DataFrame
customer_aisle_segs_predict_df.head()

aisle    air fresheners candles  asian foods  baby accessories  \
user_id                                                          
1                           0.0     0.000000               0.0   
2                           0.0     0.015385               0.0   
3                           0.0     0.000000               0.0   
4                           0.0     0.000000               0.0   
5                           0.0     0.054054               0.0   

aisle    baby bath body care  baby food formula  bakery desserts  \
user_id                                                            
1                        0.0                0.0              0.0   
2                        0.0                0.0              0.0   
3                        0.0                0.0              0.0   
4                        0.0                0.0              0.0   
5                        0.0                0.0              0.0   

aisle    baking ingredients  baking supplies decor  beauty  beers coolers  \
user_id                                                                     
1                  0.000000                    0.0     0.0            0.0   
2                  0.010256                    0.0     0.0            0.0   
3                  0.000000                    0.0     0.0            0.0   
4                  0.000000                    0.0     0.0            0.0   
5                  0.000000                    0.0     0.0            0.0   

aisle    ...       tea  tofu meat alternatives  tortillas flat bread  \
user_id  ...                                                           
1        ...  0.000000                0.000000              0.000000   
2        ...  0.005128                0.005128              0.000000   
3        ...  0.011364                0.000000              0.000000   
4        ...  0.000000                0.000000              0.055556   
5        ...  0.000000                0.000000              0.000000   

aisle    trail mix snack mix  trash bags liners  vitamins supplements  \
user_id                                                                 
1                        0.0                0.0                   0.0   
2                        0.0                0.0                   0.0   
3                        0.0                0.0                   0.0   
4                        0.0                0.0                   0.0   
5                        0.0                0.0                   0.0   

aisle    water seltzer sparkling water  white wines    yogurt  \
user_id                                                         
1                             0.000000          0.0  0.016949   
2                             0.010256          0.0  0.215385   
3                             0.022727          0.0  0.000000   
4                             0.055556          0.0  0.000000   
5                             0.000000          0.0  0.081081   

aisle    customer_segments  
user_id                     
1                       18  
2                       19  
3                        7  
4                        2  
5                        7  

[5 rows x 135 columns]

In [53]:
#how many customer in each segment
customer_aisle_segs_predict_df['customer_segments'].value_counts()

customer_segments
13    29310
3     28839
21    23391
4     20551
16    18919
19    13140
22     8704
23     7782
9      7713
7      7370
10     5883
24     5605
18     4565
2      4250
1      3551
17     2877
11     2385
6      2281
14     2281
8      1849
20     1398
15      974
0       961
5       849
12      781
Name: count, dtype: int64

In [54]:
# DEPARTMENT PIVOT TABLE 2 (Deparment row data normalized)

In [55]:
#department row data normalized
department_pivot_table_2 = department_pivot_table.div(department_pivot_table.sum(axis=1), axis=0)
department_pivot_table_2

department    bakery  beverages  breakfast  canned goods  dairy eggs  \
user_id                                                                
1           0.000000   0.220339   0.050847      0.000000    0.220339   
2           0.010256   0.046154   0.015385      0.005128    0.246154   
3           0.000000   0.034091   0.000000      0.000000    0.238636   
4           0.125000   0.187500   0.000000      0.062500    0.000000   
5           0.000000   0.000000   0.000000      0.027027    0.216216   
...              ...        ...        ...           ...         ...   
206205      0.066667   0.033333   0.000000      0.000000    0.466667   
206206      0.007042   0.116197   0.003521      0.031690    0.137324   
206207      0.013514   0.090090   0.018018      0.049550    0.234234   
206208      0.092262   0.029762   0.025298      0.016369    0.239583   
206209      0.069767   0.077519   0.069767      0.054264    0.217054   

department      deli  dry goods pasta    frozen  household  international  \
user_id                                                                     
1           0.000000         0.000000  0.000000   0.033898       0.000000   
2           0.107692         0.000000  0.087179   0.000000       0.015385   
3           0.022727         0.045455  0.068182   0.011364       0.000000   
4           0.125000         0.000000  0.187500   0.125000       0.000000   
5           0.027027         0.027027  0.054054   0.000000       0.054054   
...              ...              ...       ...        ...            ...   
206205      0.100000         0.000000  0.066667   0.000000       0.000000   
206206      0.017606         0.003521  0.267606   0.042254       0.014085   
206207      0.036036         0.036036  0.094595   0.000000       0.004505   
206208      0.041667         0.025298  0.038690   0.008929       0.004464   
206209      0.046512         0.023256  0.015504   0.108527       0.007752   

department  meat seafood    pantry  personal care   produce    snacks  
user_id                                                                
1               0.000000  0.016949       0.000000  0.084746  0.372881  
2               0.005128  0.056410       0.005128  0.184615  0.215385  
3               0.000000  0.045455       0.000000  0.431818  0.102273  
4               0.000000  0.000000       0.000000  0.125000  0.062500  
5               0.000000  0.054054       0.000000  0.513514  0.027027  
...                  ...       ...            ...       ...       ...  
206205          0.033333  0.000000       0.000000  0.233333  0.000000  
206206          0.007042  0.049296       0.035211  0.119718  0.147887  
206207          0.027027  0.067568       0.000000  0.225225  0.103604  
206208          0.032738  0.056548       0.007440  0.293155  0.087798  
206209          0.015504  0.062016       0.000000  0.147287  0.085271  

[206140 rows x 15 columns]

In [56]:
department_pivot_table_2.columns

Index(['bakery', 'beverages', 'breakfast', 'canned goods', 'dairy eggs',
       'deli', 'dry goods pasta', 'frozen', 'household', 'international',
       'meat seafood', 'pantry', 'personal care', 'produce', 'snacks'],
      dtype='object', name='department')

In [57]:
# DEPARTMENT ELBOW CURVE

In [58]:
#create a list to store inertia values
dept_inertia = []

#create a list to store the values of k
dept_k = list(range(1, 25))

In [59]:
# Create a for-loop where each value of k is evaluated using the K-means algorithm
# Fit the model using the spread_df DataFrame
# Append the value of the computed inertia from the `inertia_` attribute of the KMeans model instance

for i in dept_k:
    kmeans = KMeans(n_clusters=i, random_state=0)
    kmeans.fit(department_pivot_table_2)
    dept_inertia.append(kmeans.inertia_)

In [60]:
# Create a Dictionary that holds the list values for k and inertia
dept_elbow_data = {"k": dept_k, "inertia": dept_inertia}

# Create a DataFrame using the elbow_data Dictionary
dept_df_elbow = pd.DataFrame(dept_elbow_data)

# Review the DataFrame
dept_df_elbow

k       inertia
0    1  20909.170825
1    2  15586.797591
2    3  13673.666405
3    4  12572.494400
4    5  11408.234497
5    6  10539.687627
6    7  10005.001225
7    8   9540.520559
8    9   9079.828618
9   10   8742.556215
10  11   8416.518637
11  12   8212.918544
12  13   8018.800153
13  14   7855.186914
14  15   7659.913108
15  16   7532.558719
16  17   7413.603787
17  18   7248.732395
18  19   7129.918499
19  20   6998.405237
20  21   6910.608614
21  22   6805.311783
22  23   6713.507731
23  24   6623.355749

In [61]:
dept_inertia

[20909.17082509098,
 15586.797590518716,
 13673.6664053489,
 12572.494400426007,
 11408.234496804747,
 10539.687627366682,
 10005.001224588692,
 9540.520558802136,
 9079.82861815879,
 8742.55621483528,
 8416.518636855484,
 8212.91854391189,
 8018.800152946678,
 7855.186913680026,
 7659.913108183493,
 7532.558718803701,
 7413.60378688472,
 7248.732394712731,
 7129.918499241035,
 6998.405236941059,
 6910.608613945554,
 6805.311782854731,
 6713.507731263041,
 6623.355748736298]

In [62]:
# Plot the DataFrame
dept_df_elbow.hvplot.line(
    x="k",
    y="inertia",
    title="Elbow Curve",
    xticks=k
)

:Curve   [k]   (inertia)

In [63]:
# MACHINE LEARNING FOR DEPARTMENTS, 6 clusters chosen from Elbow Curve

In [64]:
#setting up the deparments clustering, create and initialize the K-means model for 4 clusters
model = KMeans(n_clusters=6, random_state=1)
model

KMeans(n_clusters=6, random_state=1)

In [65]:
#fit the data to the instance of the model
model.fit(department_pivot_table_2)

KMeans(n_clusters=6, random_state=1)

In [66]:
#make predictions about the data cluster the pivot table
customer_dept_segments = model.predict(department_pivot_table_2)
customer_dept_segments

array([1, 3, 0, ..., 3, 0, 5])

In [67]:
# create a copy of the DataFrame
customer_dept_segs_predict_df = department_pivot_table_2.copy()

# Add a column to the DataFrame that conains the customer_segmentation information
customer_dept_segs_predict_df['customer segment'] = customer_dept_segments

# review the DataFrame
customer_dept_segs_predict_df.head()

department    bakery  beverages  breakfast  canned goods  dairy eggs  \
user_id                                                                
1           0.000000   0.220339   0.050847      0.000000    0.220339   
2           0.010256   0.046154   0.015385      0.005128    0.246154   
3           0.000000   0.034091   0.000000      0.000000    0.238636   
4           0.125000   0.187500   0.000000      0.062500    0.000000   
5           0.000000   0.000000   0.000000      0.027027    0.216216   

department      deli  dry goods pasta    frozen  household  international  \
user_id                                                                     
1           0.000000         0.000000  0.000000   0.033898       0.000000   
2           0.107692         0.000000  0.087179   0.000000       0.015385   
3           0.022727         0.045455  0.068182   0.011364       0.000000   
4           0.125000         0.000000  0.187500   0.125000       0.000000   
5           0.027027         0.027027  0.054054   0.000000       0.054054   

department  meat seafood    pantry  personal care   produce    snacks  \
user_id                                                                 
1               0.000000  0.016949       0.000000  0.084746  0.372881   
2               0.005128  0.056410       0.005128  0.184615  0.215385   
3               0.000000  0.045455       0.000000  0.431818  0.102273   
4               0.000000  0.000000       0.000000  0.125000  0.062500   
5               0.000000  0.054054       0.000000  0.513514  0.027027   

department  customer segment  
user_id                       
1                          1  
2                          3  
3                          0  
4                          5  
5                          2

In [68]:
customer_dept_segs_predict_df['customer segment'].value_counts()

customer segment
0    77024
5    50111
2    32885
3    25817
4    10235
1    10068
Name: count, dtype: int64

In [69]:
segment_0 = customer_dept_segs_predict_df[customer_dept_segs_predict_df['customer segment'] == 0]
segment_1 = customer_dept_segs_predict_df[customer_dept_segs_predict_df['customer segment'] == 1]
segment_2 = customer_dept_segs_predict_df[customer_dept_segs_predict_df['customer segment'] == 2]
segment_3 = customer_dept_segs_predict_df[customer_dept_segs_predict_df['customer segment'] == 3]
segment_4 = customer_dept_segs_predict_df[customer_dept_segs_predict_df['customer segment'] == 4]
segment_5 = customer_dept_segs_predict_df[customer_dept_segs_predict_df['customer segment'] == 5]

In [70]:
segment_0.sample(n=20).round(3)

department  bakery  beverages  breakfast  canned goods  dairy eggs   deli  \
user_id                                                                     
109985       0.038      0.066      0.000         0.057       0.208  0.085   
19768        0.043      0.000      0.000         0.174       0.174  0.000   
173901       0.024      0.153      0.024         0.081       0.081  0.065   
140188       0.062      0.000      0.041         0.027       0.212  0.014   
127892       0.015      0.096      0.000         0.051       0.191  0.040   
44502        0.089      0.063      0.000         0.013       0.228  0.013   
113878       0.014      0.127      0.014         0.014       0.099  0.000   
172669       0.013      0.000      0.079         0.000       0.184  0.000   
13322        0.043      0.000      0.000         0.074       0.213  0.011   
14664        0.017      0.008      0.008         0.017       0.203  0.008   
66146        0.125      0.107      0.018         0.000       0.196  0.071   
5860         0.009      0.062      0.016         0.077       0.083  0.071   
193929       0.013      0.013      0.007         0.013       0.187  0.047   
81411        0.023      0.091      0.000         0.068       0.159  0.091   
91714        0.133      0.067      0.200         0.000       0.067  0.000   
143475       0.008      0.000      0.000         0.000       0.113  0.000   
124142       0.028      0.028      0.042         0.127       0.085  0.000   
194457       0.075      0.050      0.000         0.000       0.300  0.025   
121995       0.000      0.011      0.000         0.098       0.196  0.022   
161565       0.037      0.148      0.000         0.000       0.037  0.000   

department  dry goods pasta  frozen  household  international  meat seafood  \
user_id                                                                       
109985                0.000   0.000      0.057          0.000         0.009   
19768                 0.000   0.130      0.000          0.000         0.043   
173901                0.016   0.032      0.000          0.000         0.000   
140188                0.041   0.007      0.007          0.000         0.034   
127892                0.015   0.059      0.015          0.000         0.048   
44502                 0.076   0.025      0.051          0.013         0.000   
113878                0.042   0.056      0.000          0.056         0.042   
172669                0.013   0.013      0.000          0.079         0.132   
13322                 0.021   0.021      0.000          0.000         0.053   
14664                 0.068   0.144      0.000          0.000         0.068   
66146                 0.036   0.107      0.018          0.000         0.000   
5860                  0.075   0.149      0.008          0.018         0.012   
193929                0.007   0.140      0.067          0.000         0.040   
81411                 0.000   0.023      0.000          0.000         0.000   
91714                 0.133   0.000      0.000          0.000         0.000   
143475                0.145   0.000      0.032          0.024         0.194   
124142                0.028   0.099      0.014          0.028         0.028   
194457                0.000   0.000      0.000          0.000         0.000   
121995                0.022   0.087      0.000          0.120         0.000   
161565                0.000   0.037      0.000          0.000         0.000   

department  pantry  personal care  produce  snacks  customer segment  
user_id                                                               
109985       0.047          0.009    0.396   0.028                 0  
19768        0.087          0.000    0.348   0.000                 0  
173901       0.000          0.008    0.371   0.145                 0  
140188       0.034          0.014    0.438   0.068                 0  
127892       0.081          0.015    0.338   0.037                 0  
44502        0.101          0.013    0.253   0.063                 0 

In [71]:
segment_0.describe().round(3)

department     bakery  beverages  breakfast  canned goods  dairy eggs  \
count       77024.000  77024.000  77024.000     77024.000   77024.000   
mean            0.036      0.067      0.019         0.039       0.160   
std             0.038      0.063      0.029         0.042       0.069   
min             0.000      0.000      0.000         0.000       0.000   
25%             0.006      0.020      0.000         0.008       0.113   
50%             0.027      0.053      0.009         0.029       0.160   
75%             0.053      0.097      0.028         0.056       0.206   
max             0.722      0.412      0.750         0.800       0.453   

department       deli  dry goods pasta     frozen  household  international  \
count       77024.000        77024.000  77024.000  77024.000      77024.000   
mean            0.036            0.029      0.065      0.017          0.010   
std             0.041            0.033      0.057      0.032          0.018   
min             0.000            0.000      0.000      0.000          0.000   
25%             0.005            0.000      0.024      0.000          0.000   
50%             0.026            0.022      0.054      0.004          0.000   
75%             0.052            0.043      0.092      0.022          0.013   
max             0.708            0.667      0.600      0.667          0.467   

department  meat seafood     pantry  personal care    produce     snacks  \
count          77024.000  77024.000      77024.000  77024.000  77024.000   
mean               0.027      0.064          0.011      0.347      0.072   
std                0.035      0.051          0.023      0.066      0.058   
min                0.000      0.000          0.000      0.167      0.000   
25%                0.000      0.030          0.000      0.294      0.029   
50%                0.017      0.056          0.000      0.346      0.061   
75%                0.039      0.087          0.014      0.400      0.103   
max                0.700      0.750          0.667      0.500      0.412   

department  customer segment  
count                77024.0  
mean                     0.0  
std                      0.0  
min                      0.0  
25%                      0.0  
50%                      0.0  
75%                      0.0  
max                      0.0

In [72]:
segment_1.sample(n=20).round(3)

department  bakery  beverages  breakfast  canned goods  dairy eggs   deli  \
user_id                                                                     
54577        0.007      0.081      0.081         0.118       0.103  0.000   
59177        0.000      0.190      0.000         0.000       0.190  0.000   
195576       0.000      0.298      0.000         0.000       0.000  0.000   
118712       0.043      0.130      0.022         0.000       0.109  0.043   
64880        0.000      0.091      0.000         0.000       0.000  0.000   
60946        0.000      0.312      0.000         0.000       0.000  0.000   
171721       0.344      0.000      0.062         0.000       0.156  0.000   
34770        0.158      0.000      0.000         0.000       0.053  0.000   
75406        0.043      0.043      0.000         0.000       0.000  0.000   
96909        0.000      0.125      0.042         0.000       0.208  0.000   
157837       0.000      0.194      0.129         0.000       0.161  0.000   
185935       0.000      0.000      0.000         0.000       0.000  0.000   
175216       0.041      0.106      0.092         0.000       0.174  0.000   
143059       0.130      0.304      0.000         0.000       0.130  0.109   
155015       0.050      0.151      0.029         0.007       0.072  0.058   
135504       0.000      0.000      0.000         0.000       0.000  0.071   
166117       0.020      0.275      0.000         0.078       0.078  0.118   
35452        0.019      0.000      0.132         0.000       0.038  0.000   
107324       0.018      0.018      0.055         0.000       0.273  0.055   
14660        0.000      0.283      0.000         0.000       0.000  0.000   

department  dry goods pasta  frozen  household  international  meat seafood  \
user_id                                                                       
54577                 0.015   0.044      0.007          0.000         0.007   
59177                 0.000   0.000      0.000          0.000         0.000   
195576                0.000   0.000      0.043          0.000         0.000   
118712                0.043   0.000      0.000          0.000         0.000   
64880                 0.000   0.091      0.000          0.000         0.000   
60946                 0.000   0.000      0.062          0.000         0.000   
171721                0.031   0.000      0.000          0.000         0.000   
34770                 0.000   0.053      0.158          0.000         0.053   
75406                 0.000   0.000      0.087          0.000         0.000   
96909                 0.000   0.000      0.000          0.042         0.000   
157837                0.000   0.000      0.097          0.000         0.000   
185935                0.125   0.000      0.125          0.000         0.000   
175216                0.000   0.005      0.000          0.000         0.000   
143059                0.000   0.000      0.000          0.000         0.000   
155015                0.000   0.058      0.000          0.014         0.000   
135504                0.000   0.071      0.000          0.000         0.000   
166117                0.000   0.039      0.078          0.000         0.000   
35452                 0.019   0.094      0.000          0.000         0.000   
107324                0.000   0.000      0.027          0.009         0.000   
14660                 0.000   0.000      0.050          0.000         0.000   

department  pantry  personal care  produce  snacks  customer segment  
user_id                                                               
54577        0.140          0.000    0.044   0.353                 1  
59177        0.095          0.000    0.238   0.286                 1  
195576       0.000          0.000    0.340   0.319                 1  
118712       0.000          0.000    0.304   0.304                 1  
64880        0.182          0.091    0.000   0.545                 1  
60946        0.125          0.000    0.125   0.375                 1 

In [73]:
segment_1.describe().round(3)

department     bakery  beverages  breakfast  canned goods  dairy eggs  \
count       10068.000  10068.000  10068.000     10068.000   10068.000   
mean            0.025      0.131      0.034         0.011       0.095   
std             0.047      0.112      0.060         0.031       0.089   
min             0.000      0.000      0.000         0.000       0.000   
25%             0.000      0.031      0.000         0.000       0.000   
50%             0.000      0.112      0.000         0.000       0.081   
75%             0.033      0.210      0.048         0.000       0.153   
max             0.697      0.500      0.750         0.438       0.533   

department       deli  dry goods pasta     frozen  household  international  \
count       10068.000        10068.000  10068.000  10068.000      10068.000   
mean            0.029            0.009      0.038      0.029          0.004   
std             0.056            0.026      0.063      0.057          0.016   
min             0.000            0.000      0.000      0.000          0.000   
25%             0.000            0.000      0.000      0.000          0.000   
50%             0.000            0.000      0.000      0.000          0.000   
75%             0.037            0.000      0.056      0.035          0.000   
max             0.566            0.333      0.500      0.667          0.308   

department  meat seafood     pantry  personal care    produce     snacks  \
count          10068.000  10068.000      10068.000  10068.000  10068.000   
mean               0.008      0.043          0.016      0.111      0.418   
std                0.029      0.060          0.042      0.103      0.159   
min                0.000      0.000          0.000      0.000      0.200   
25%                0.000      0.000          0.000      0.013      0.304   
50%                0.000      0.023          0.000      0.091      0.371   
75%                0.000      0.061          0.012      0.177      0.486   
max                0.750      0.667          0.714      0.518      1.000   

department  customer segment  
count                10068.0  
mean                     1.0  
std                      0.0  
min                      1.0  
25%                      1.0  
50%                      1.0  
75%                      1.0  
max                      1.0

In [74]:
segment_2.sample(n=20).round(3)

department  bakery  beverages  breakfast  canned goods  dairy eggs   deli  \
user_id                                                                     
8453         0.010      0.045      0.010         0.000       0.095  0.080   
54368        0.054      0.071      0.000         0.036       0.036  0.000   
49696        0.000      0.000      0.000         0.000       0.067  0.000   
28998        0.014      0.101      0.000         0.000       0.145  0.000   
91297        0.000      0.088      0.000         0.015       0.059  0.000   
14875        0.188      0.000      0.000         0.000       0.125  0.000   
96440        0.000      0.018      0.000         0.018       0.140  0.000   
123595       0.000      0.000      0.000         0.000       0.182  0.000   
69937        0.002      0.015      0.006         0.023       0.126  0.013   
159786       0.100      0.000      0.006         0.006       0.100  0.047   
61523        0.053      0.053      0.000         0.053       0.158  0.053   
35252        0.014      0.055      0.068         0.164       0.068  0.014   
186518       0.000      0.056      0.083         0.000       0.056  0.111   
109267       0.000      0.000      0.000         0.000       0.160  0.000   
97962        0.000      0.000      0.029         0.029       0.114  0.000   
139136       0.018      0.023      0.000         0.018       0.041  0.018   
91880        0.064      0.000      0.045         0.020       0.211  0.000   
25740        0.000      0.000      0.000         0.000       0.000  0.000   
153870       0.000      0.000      0.000         0.000       0.045  0.051   
132552       0.000      0.000      0.000         0.000       0.000  0.000   

department  dry goods pasta  frozen  household  international  meat seafood  \
user_id                                                                       
8453                  0.000   0.090      0.025          0.000         0.015   
54368                 0.018   0.036      0.054          0.054         0.036   
49696                 0.067   0.000      0.000          0.000         0.000   
28998                 0.000   0.014      0.000          0.000         0.043   
91297                 0.000   0.044      0.000          0.000         0.000   
14875                 0.000   0.125      0.000          0.000         0.000   
96440                 0.000   0.035      0.000          0.000         0.018   
123595                0.000   0.091      0.000          0.000         0.000   
69937                 0.021   0.044      0.027          0.002         0.040   
159786                0.000   0.006      0.000          0.000         0.000   
61523                 0.000   0.000      0.000          0.000         0.053   
35252                 0.027   0.000      0.000          0.027         0.000   
186518                0.000   0.000      0.000          0.000         0.000   
109267                0.040   0.040      0.000          0.000         0.000   
97962                 0.000   0.143      0.000          0.000         0.000   
139136                0.000   0.058      0.029          0.070         0.006   
91880                 0.024   0.005      0.014          0.004         0.018   
25740                 0.000   0.000      0.000          0.000         0.000   
153870                0.051   0.017      0.000          0.000         0.051   
132552                0.000   0.000      0.000          0.000         0.000   

department  pantry  personal care  produce  snacks  customer segment  
user_id                                                               
8453         0.020          0.000    0.470   0.140                 2  
54368        0.089          0.000    0.464   0.054                 2  
49696        0.067          0.000    0.800   0.000                 2  
28998        0.000          0.000    0.667   0.014                 2  
91297        0.029          0.000    0.765   0.000                 2  
14875        0.000          0.000    0.562   0.000                 2 

In [75]:
segment_2.describe().round(3)

department     bakery  beverages  breakfast  canned goods  dairy eggs  \
count       32885.000  32885.000  32885.000     32885.000   32885.000   
mean            0.020      0.043      0.010         0.028       0.106   
std             0.033      0.056      0.023         0.037       0.076   
min             0.000      0.000      0.000         0.000       0.000   
25%             0.000      0.000      0.000         0.000       0.049   
50%             0.005      0.024      0.000         0.015       0.100   
75%             0.030      0.062      0.012         0.043       0.153   
max             0.500      0.462      0.462         0.500       0.474   

department       deli  dry goods pasta     frozen  household  international  \
count       32885.000        32885.000  32885.000  32885.000      32885.000   
mean            0.022            0.016      0.038      0.010          0.006   
std             0.034            0.026      0.047      0.027          0.015   
min             0.000            0.000      0.000      0.000          0.000   
25%             0.000            0.000      0.000      0.000          0.000   
50%             0.008            0.003      0.024      0.000          0.000   
75%             0.033            0.025      0.056      0.010          0.006   
max             0.556            0.500      0.500      0.500          0.333   

department  meat seafood     pantry  personal care    produce     snacks  \
count          32885.000  32885.000      32885.000  32885.000  32885.000   
mean               0.021      0.045          0.007      0.585      0.043   
std                0.034      0.046          0.018      0.110      0.052   
min                0.000      0.000          0.000      0.429      0.000   
25%                0.000      0.009          0.000      0.500      0.000   
50%                0.004      0.036          0.000      0.553      0.028   
75%                0.031      0.066          0.004      0.634      0.062   
max                0.571      0.545          0.429      1.000      0.462   

department  customer segment  
count                32885.0  
mean                     2.0  
std                      0.0  
min                      2.0  
25%                      2.0  
50%                      2.0  
75%                      2.0  
max                      2.0

In [76]:
segment_3.sample(n=20).round(3)

department  bakery  beverages  breakfast  canned goods  dairy eggs   deli  \
user_id                                                                     
56753        0.000      0.039      0.020         0.098       0.431  0.000   
163367       0.000      0.000      0.217         0.000       0.435  0.000   
49855        0.093      0.183      0.006         0.013       0.251  0.077   
161798       0.100      0.000      0.000         0.000       0.300  0.000   
116978       0.029      0.059      0.000         0.088       0.324  0.000   
189163       0.200      0.080      0.000         0.000       0.280  0.120   
549          0.063      0.089      0.013         0.038       0.241  0.025   
4229         0.060      0.033      0.000         0.000       0.266  0.195   
75285        0.333      0.000      0.222         0.000       0.222  0.000   
75394        0.010      0.217      0.015         0.020       0.303  0.035   
16237        0.023      0.000      0.000         0.017       0.289  0.046   
184165       0.085      0.138      0.015         0.015       0.238  0.000   
136050       0.030      0.110      0.040         0.040       0.380  0.010   
91678        0.017      0.079      0.056         0.056       0.237  0.073   
81380        0.000      0.035      0.035         0.047       0.400  0.012   
74571        0.015      0.044      0.110         0.051       0.213  0.000   
98054        0.080      0.000      0.000         0.000       0.705  0.125   
7612         0.070      0.022      0.026         0.017       0.288  0.057   
133203       0.000      0.000      0.000         0.000       0.688  0.000   
146649       0.056      0.006      0.000         0.000       0.636  0.099   

department  dry goods pasta  frozen  household  international  meat seafood  \
user_id                                                                       
56753                 0.039   0.000      0.000          0.000         0.157   
163367                0.043   0.000      0.000          0.000         0.000   
49855                 0.029   0.013      0.016          0.000         0.045   
161798                0.000   0.000      0.000          0.000         0.100   
116978                0.000   0.000      0.059          0.000         0.088   
189163                0.000   0.000      0.000          0.000         0.080   
549                   0.038   0.038      0.025          0.051         0.013   
4229                  0.000   0.032      0.000          0.008         0.000   
75285                 0.000   0.000      0.000          0.000         0.000   
75394                 0.010   0.000      0.030          0.000         0.051   
16237                 0.139   0.006      0.000          0.000         0.110   
184165                0.054   0.054      0.008          0.000         0.023   
136050                0.040   0.230      0.050          0.000         0.000   
91678                 0.051   0.040      0.006          0.011         0.023   
81380                 0.047   0.082      0.000          0.000         0.000   
74571                 0.169   0.096      0.000          0.000         0.000   
98054                 0.000   0.000      0.000          0.000         0.011   
7612                  0.061   0.083      0.000          0.013         0.061   
133203                0.000   0.062      0.000          0.000         0.125   
146649                0.000   0.019      0.000          0.000         0.043   

department  pantry  personal care  produce  snacks  customer segment  
user_id                                                               
56753        0.098          0.000    0.118   0.000                 3  
163367       0.000          0.000    0.304   0.000                 3  
49855        0.039          0.000    0.158   0.077                 3  
161798       0.200          0.000    0.300   0.000                 3  
116978       0.059          0.000    0.206   0.088                 3  
189163       0.000          0.000    0.200   0.040                 3 

In [77]:
segment_3.describe().round(3)

department     bakery  beverages  breakfast  canned goods  dairy eggs  \
count       25817.000  25817.000  25817.000     25817.000   25817.000   
mean            0.043      0.075      0.027         0.026       0.347   
std             0.051      0.075      0.045         0.039       0.121   
min             0.000      0.000      0.000         0.000       0.179   
25%             0.000      0.014      0.000         0.000       0.269   
50%             0.029      0.056      0.010         0.011       0.315   
75%             0.066      0.111      0.038         0.040       0.383   
max             0.600      0.455      0.678         0.667       1.000   

department       deli  dry goods pasta     frozen  household  international  \
count       25817.000        25817.000  25817.000  25817.000      25817.000   
mean            0.032            0.024      0.056      0.021          0.007   
std             0.045            0.036      0.061      0.040          0.018   
min             0.000            0.000      0.000      0.000          0.000   
25%             0.000            0.000      0.000      0.000          0.000   
50%             0.017            0.010      0.042      0.000          0.000   
75%             0.047            0.037      0.086      0.026          0.006   
max             0.750            0.524      0.571      0.667          0.486   

department  meat seafood     pantry  personal care    produce     snacks  \
count          25817.000  25817.000      25817.000  25817.000  25817.000   
mean               0.020      0.057          0.013      0.178      0.072   
std                0.036      0.059          0.030      0.094      0.067   
min                0.000      0.000          0.000      0.000      0.000   
25%                0.000      0.016          0.000      0.115      0.018   
50%                0.000      0.045          0.000      0.186      0.058   
75%                0.029      0.081          0.014      0.241      0.109   
max                0.600      0.667          0.667      0.506      0.412   

department  customer segment  
count                25817.0  
mean                     3.0  
std                      0.0  
min                      3.0  
25%                      3.0  
50%                      3.0  
75%                      3.0  
max                      3.0

In [78]:
segment_4.sample(n=20).round(3)

department  bakery  beverages  breakfast  canned goods  dairy eggs   deli  \
user_id                                                                     
151759       0.006      0.402      0.017         0.000       0.106  0.022   
172623       0.018      0.456      0.018         0.018       0.175  0.000   
149085       0.000      0.331      0.006         0.000       0.184  0.147   
117052       0.000      0.333      0.000         0.048       0.095  0.143   
101758       0.006      0.341      0.000         0.031       0.130  0.022   
46762        0.000      0.291      0.091         0.055       0.055  0.000   
23394        0.067      0.400      0.000         0.133       0.200  0.000   
73046        0.000      0.474      0.000         0.000       0.000  0.000   
178153       0.059      0.412      0.088         0.000       0.324  0.000   
190326       0.006      0.518      0.082         0.000       0.306  0.047   
171251       0.000      0.875      0.000         0.000       0.125  0.000   
143094       0.000      0.500      0.000         0.000       0.000  0.000   
132403       0.000      0.308      0.026         0.000       0.077  0.000   
30778        0.000      0.714      0.000         0.000       0.000  0.000   
186395       0.000      1.000      0.000         0.000       0.000  0.000   
30343        0.000      1.000      0.000         0.000       0.000  0.000   
42505        0.000      0.420      0.000         0.000       0.020  0.020   
164897       0.000      0.789      0.000         0.000       0.000  0.000   
183587       0.000      0.406      0.031         0.000       0.344  0.000   
115723       0.000      0.571      0.000         0.000       0.000  0.000   

department  dry goods pasta  frozen  household  international  meat seafood  \
user_id                                                                       
151759                0.000   0.006      0.017          0.000         0.000   
172623                0.018   0.018      0.000          0.018         0.053   
149085                0.000   0.000      0.025          0.012         0.000   
117052                0.000   0.143      0.000          0.000         0.000   
101758                0.000   0.040      0.087          0.022         0.102   
46762                 0.018   0.018      0.091          0.000         0.018   
23394                 0.000   0.000      0.000          0.000         0.000   
73046                 0.000   0.105      0.000          0.000         0.000   
178153                0.000   0.088      0.029          0.000         0.000   
190326                0.000   0.000      0.000          0.006         0.000   
171251                0.000   0.000      0.000          0.000         0.000   
143094                0.000   0.000      0.231          0.000         0.000   
132403                0.000   0.000      0.385          0.000         0.000   
30778                 0.000   0.000      0.000          0.000         0.000   
186395                0.000   0.000      0.000          0.000         0.000   
30343                 0.000   0.000      0.000          0.000         0.000   
42505                 0.000   0.000      0.020          0.000         0.000   
164897                0.000   0.053      0.000          0.000         0.000   
183587                0.000   0.000      0.062          0.000         0.000   
115723                0.000   0.190      0.000          0.000         0.000   

department  pantry  personal care  produce  snacks  customer segment  
user_id                                                               
151759       0.022          0.006    0.067   0.330                 4  
172623       0.018          0.000    0.053   0.140                 4  
149085       0.018          0.006    0.092   0.178                 4  
117052       0.048          0.048    0.143   0.000                 4  
101758       0.043          0.009    0.115   0.053                 4  
46762        0.091          0.055    0.000   0.218                 4 

In [79]:
segment_4.describe().round(3)

department     bakery  beverages  breakfast  canned goods  dairy eggs  \
count       10235.000  10235.000  10235.000     10235.000   10235.000   
mean            0.018      0.510      0.017         0.011       0.084   
std             0.045      0.186      0.043         0.036       0.093   
min             0.000      0.275      0.000         0.000       0.000   
25%             0.000      0.369      0.000         0.000       0.000   
50%             0.000      0.450      0.000         0.000       0.059   
75%             0.018      0.600      0.013         0.000       0.138   
max             0.667      1.000      0.529         0.700       0.500   

department       deli  dry goods pasta     frozen  household  international  \
count       10235.000        10235.000  10235.000  10235.000      10235.000   
mean            0.015            0.007      0.035      0.052          0.004   
std             0.040            0.025      0.067      0.093          0.016   
min             0.000            0.000      0.000      0.000          0.000   
25%             0.000            0.000      0.000      0.000          0.000   
50%             0.000            0.000      0.000      0.001          0.000   
75%             0.010            0.000      0.047      0.067          0.000   
max             0.714            0.455      0.600      0.714          0.318   

department  meat seafood     pantry  personal care    produce     snacks  \
count          10235.000  10235.000      10235.000  10235.000  10235.000   
mean               0.009      0.038          0.022      0.087      0.090   
std                0.032      0.061          0.053      0.102      0.098   
min                0.000      0.000          0.000      0.000      0.000   
25%                0.000      0.000          0.000      0.000      0.000   
50%                0.000      0.010          0.000      0.050      0.062   
75%                0.000      0.053          0.018      0.145      0.150   
max                0.545      0.667          0.667      0.500      0.483   

department  customer segment  
count                10235.0  
mean                     4.0  
std                      0.0  
min                      4.0  
25%                      4.0  
50%                      4.0  
75%                      4.0  
max                      4.0

In [80]:
segment_5.sample(n=20).round(3)

department  bakery  beverages  breakfast  canned goods  dairy eggs   deli  \
user_id                                                                     
101143       0.000      0.156      0.028         0.057       0.156  0.000   
199323       0.000      0.143      0.000         0.000       0.000  0.000   
72347        0.043      0.059      0.005         0.092       0.114  0.054   
41464        0.126      0.004      0.032         0.166       0.094  0.249   
136552       0.000      0.000      0.000         0.000       0.000  0.000   
112358       0.070      0.000      0.023         0.070       0.209  0.186   
85302        0.000      0.111      0.000         0.000       0.056  0.000   
21095        0.047      0.102      0.026         0.015       0.233  0.035   
81639        0.094      0.156      0.021         0.042       0.052  0.031   
35843        0.115      0.058      0.021         0.004       0.177  0.070   
110094       0.143      0.000      0.000         0.071       0.000  0.000   
27344        0.043      0.029      0.005         0.029       0.155  0.019   
196772       0.045      0.080      0.020         0.065       0.104  0.005   
67702        0.060      0.034      0.034         0.021       0.234  0.004   
200774       0.013      0.184      0.044         0.055       0.247  0.000   
91634        0.026      0.167      0.005         0.109       0.115  0.016   
44149        0.043      0.137      0.071         0.014       0.095  0.019   
75084        0.043      0.130      0.000         0.174       0.087  0.000   
5374         0.050      0.238      0.010         0.020       0.119  0.040   
127575       0.051      0.092      0.010         0.048       0.197  0.044   

department  dry goods pasta  frozen  household  international  meat seafood  \
user_id                                                                       
101143                0.085   0.106      0.000          0.000         0.014   
199323                0.000   0.000      0.214          0.000         0.000   
72347                 0.016   0.081      0.103          0.032         0.054   
41464                 0.022   0.007      0.051          0.014         0.007   
136552                0.000   0.667      0.067          0.000         0.000   
112358                0.047   0.163      0.000          0.000         0.000   
85302                 0.000   0.111      0.278          0.000         0.111   
21095                 0.023   0.113      0.009          0.000         0.032   
81639                 0.062   0.083      0.104          0.000         0.052   
35843                 0.037   0.099      0.012          0.000         0.053   
110094                0.000   0.000      0.500          0.000         0.000   
27344                 0.034   0.010      0.121          0.014         0.000   
196772                0.050   0.289      0.025          0.035         0.040   
67702                 0.004   0.204      0.043          0.004         0.013   
200774                0.016   0.026      0.161          0.008         0.003   
91634                 0.068   0.141      0.016          0.031         0.031   
44149                 0.043   0.057      0.000          0.057         0.024   
75084                 0.043   0.087      0.000          0.000         0.000   
5374                  0.010   0.198      0.010          0.010         0.050   
127575                0.041   0.102      0.035          0.019         0.029   

department  pantry  personal care  produce  snacks  customer segment  
user_id                                                               
101143       0.085          0.000    0.227   0.085                 5  
199323       0.286          0.286    0.000   0.071                 5  
72347        0.114          0.043    0.119   0.070                 5  
41464        0.040          0.000    0.184   0.004                 5  
136552       0.000          0.000    0.267   0.000                 5  
112358       0.070          0.000    0.116   0.047                 5 

In [81]:
segment_5.describe().round(3)

department     bakery  beverages  breakfast  canned goods  dairy eggs  \
count       50111.000  50111.000  50111.000     50111.000   50111.000   
mean            0.047      0.111      0.031         0.040       0.129   
std             0.056      0.079      0.050         0.053       0.067   
min             0.000      0.000      0.000         0.000       0.000   
25%             0.005      0.049      0.000         0.000       0.083   
50%             0.036      0.100      0.015         0.024       0.133   
75%             0.068      0.163      0.043         0.058       0.179   
max             1.000      0.375      1.000         1.000       0.375   

department       deli  dry goods pasta     frozen  household  international  \
count       50111.000        50111.000  50111.000  50111.000      50111.000   
mean            0.036            0.034      0.133      0.066          0.010   
std             0.054            0.045      0.120      0.111          0.024   
min             0.000            0.000      0.000      0.000          0.000   
25%             0.000            0.000      0.051      0.000          0.000   
50%             0.021            0.021      0.107      0.031          0.000   
75%             0.050            0.051      0.182      0.079          0.012   
max             1.000            1.000      1.000      1.000          1.000   

department  meat seafood     pantry  personal care    produce     snacks  \
count          50111.000  50111.000      50111.000  50111.000  50111.000   
mean               0.025      0.082          0.037      0.122      0.098   
std                0.043      0.081          0.070      0.073      0.068   
min                0.000      0.000          0.000      0.000      0.000   
25%                0.000      0.032          0.000      0.062      0.044   
50%                0.010      0.065          0.013      0.128      0.091   
75%                0.037      0.108          0.043      0.182      0.145   
max                1.000      1.000          1.000      0.364      0.366   

department  customer segment  
count                50111.0  
mean                     5.0  
std                      0.0  
min                      5.0  
25%                      5.0  
50%                      5.0  
75%                      5.0  
max                      5.0

AISLE PCA

In [83]:
# Instantiate the PCA instance and declare the number of PCA variables
pca = PCA(n_components=20)

# Fit the PCA model on the transformed credit card DataFrame
customers_pca = pca.fit_transform(aisle_pivot_table_2)

# Review the first 5 rows of the array of list data
print(customers_pca[:5])


[[-0.11344283  0.03908444 -0.04286557  0.01883485 -0.08833637 -0.10452896
  -0.116397    0.08363011 -0.06247158 -0.02612927 -0.02124035 -0.01071731
  -0.05825385  0.05004926  0.05871346  0.00764235 -0.01820236  0.06305805
   0.01316898 -0.05760916]
 [-0.03698792  0.10888309 -0.06640651 -0.12326925  0.09883918 -0.03388456
  -0.0546985  -0.05337041 -0.02018622 -0.00875925  0.01931929 -0.03322267
   0.05361294  0.01555014 -0.00388305 -0.00246086 -0.00561883 -0.00395934
  -0.00303458 -0.01135022]
 [ 0.06428149  0.10396227  0.00071118 -0.01222629 -0.0469762   0.11221914
  -0.02982894  0.00777308  0.01211895  0.00202727 -0.00883431  0.08588299
  -0.04068714  0.09180159  0.01553817  0.03101018 -0.05884295  0.00366165
  -0.00311703 -0.03810351]
 [-0.09320996  0.05409145  0.00186355 -0.00397814 -0.07135019 -0.01919737
  -0.02510358 -0.03839042  0.00701134 -0.00210589 -0.0579587  -0.0535842
   0.12707829  0.03114408 -0.03940798  0.00668927 -0.00680425 -0.02006007
   0.00157875  0.03570307]
 [ 0.

In [84]:
# Create the PCA DataFrame
customers_pca_df = pd.DataFrame(
    customers_pca, 
    columns=['PCA1', 'PCA2', 'PCA3', 'PCA4', 'PCA5', 'PCA6', 'PCA7', 'PCA8', 'PCA9','PCA10', 'PCA11', 'PCA12', 'PCA13', 'PCA14', 'PCA15', 'PCA16', 'PCA17', 'PCA18', 'PCA19', 'PCA20'])


# Review the PCA DataFrame
print(customers_pca_df.head())


       PCA1      PCA2      PCA3      PCA4      PCA5      PCA6      PCA7  \
0 -0.113443  0.039084 -0.042866  0.018835 -0.088336 -0.104529 -0.116397   
1 -0.036988  0.108883 -0.066407 -0.123269  0.098839 -0.033885 -0.054698   
2  0.064281  0.103962  0.000711 -0.012226 -0.046976  0.112219 -0.029829   
3 -0.093210  0.054091  0.001864 -0.003978 -0.071350 -0.019197 -0.025104   
4  0.094629 -0.037051 -0.024951 -0.021570  0.055362  0.107659 -0.008021   

       PCA8      PCA9     PCA10     PCA11     PCA12     PCA13     PCA14  \
0  0.083630 -0.062472 -0.026129 -0.021240 -0.010717 -0.058254  0.050049   
1 -0.053370 -0.020186 -0.008759  0.019319 -0.033223  0.053613  0.015550   
2  0.007773  0.012119  0.002027 -0.008834  0.085883 -0.040687  0.091802   
3 -0.038390  0.007011 -0.002106 -0.057959 -0.053584  0.127078  0.031144   
4  0.104006  0.051584 -0.025533  0.035817 -0.011938  0.006980 -0.007499   

      PCA15     PCA16     PCA17     PCA18     PCA19     PCA20  
0  0.058713  0.007642 -0.018202  0

In [85]:
# Create a list to store inertia values and the values of k
inertia = []
k = list(range(1, 11))

# Evaluate each value of k using the K-means algorithm
for i in k:
    k_model = KMeans(n_clusters=i, random_state=0)
    k_model.fit(customers_pca_df)
    inertia.append(k_model.inertia_)


In [86]:
 #Define the model K-means model using the optimal value of k for the number of clusters.
model = KMeans(n_clusters=20, random_state=0)

# Fit the model
model.fit(customers_pca_df)

# Make predictions
k_20 = model.predict(customers_pca_df)

In [87]:
# Create a copy of the customers_pca_df DataFrame
customer_pca_predictions_df = customers_pca_df.copy()

# Add a class column with the labels
customer_pca_predictions_df["customer_segments"] = k_20

In [88]:

# Plot the clusters
customer_pca_predictions_df.hvplot.scatter(
    x="PCA1",
    y="PCA2",
    by="customer_segments"
)

:NdOverlay   [customer_segments]
   :Scatter   [PCA1]   (PCA2)